# README
I looked into a lot of segmentation/loading/downsampling techniques and tricks,
these are the final 3 best methods, I noticed that the result of downsampling is
FU****! so i looked into it and it turns out that applying a low-pass filter fixes this

In [2]:
!pip install audiosegment

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.2/66.2 kB 4.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for webrtcvad: filename=webrtcvad-2.0.10-cp312-cp312-linux_x86_64.whl size=73519 sha256=56432ea28b60d1aadbf0df1431ce2eba4bfe16ec291a961eef3c69d06dcea6ed
  Stored in directory: /root/.cache/pip/wheels/1e/d3/95/680fa3b16848f1a58d2edaed34c496224c89a9bc63e17b3614
Successfully built webrtcvad


In [3]:
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from pathlib import Path
import shutil


from tqdm import tqdm
from pathlib import Path
import librosa
import audiosegment
from pydub import AudioSegment
from pydub.utils import make_chunks

import scipy.signal
import soundfile as sf

/usr/local/lib/python3.12/dist-packages/pydub/utils.py:300: SyntaxWarning: invalid escape sequence '\('
  m = re.match('([su]([0-9]{1,2})p?) \(([0-9]{1,2}) bit\)$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:301: SyntaxWarning: invalid escape sequence '\('
  m2 = re.match('([su]([0-9]{1,2})p?)( \(default\))?$', token)
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:310: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(flt)p?( \(default\))?$', token):
/usr/local/lib/python3.12/dist-packages/pydub/utils.py:314: SyntaxWarning: invalid escape sequence '\('
  elif re.match('(dbl)p?( \(default\))?$', token):


### Choosing a resampling method

In [11]:
audioFile = "222524.wav" # path of a random test recording clip of the humbug db
#we'll do the full loading -> downsampling -> ? -> saving pipeline on this 3 times

#### 1- normal librosa load&downsample but with polyphase

In [12]:
audio, _ = librosa.load(audioFile, sr=None,res_type="polyphase")

audio = audiosegment.from_numpy_array(audio, 16_000)
chunks= make_chunks(audio, 1000)
#export one chunk
if os.path.exists('test.wav'):
  os.remove('test.wav')
chunks[0].export('segment (first pipeline).wav', format='wav')

<_io.BufferedRandom name='segment (first pipeline).wav'>

#### 2- Audiotorch load and resample

In [13]:
import torchaudio
import torch

resampler = torchaudio.transforms.Resample(orig_freq=44100, new_freq=16_000)

#load the audio file using torchaudio.
audio, _ = torchaudio.load(audioFile)
audio    = resampler(audio).numpy().squeeze(0)

result   = audiosegment.from_numpy_array(audio, 16_000)
chunks   = make_chunks(result, 1000)

#export one chunk
if os.path.exists('segment (second pipeline).wav'):
  os.remove('segment (second pipeline).wav')
chunks[0].export('segment (second pipeline).wav', format='wav')

/usr/local/lib/python3.12/dist-packages/torchaudio/_backend/utils.py:213: UserWarning: In 2.9, this function's implementation will be changed to use torchaudio.load_with_torchcodec` under the hood. Some parameters like ``normalize``, ``format``, ``buffer_size``, and ``backend`` will be ignored. We recommend that you port your code to rely directly on TorchCodec's decoder instead: https://docs.pytorch.org/torchcodec/stable/generated/torchcodec.decoders.AudioDecoder.html#torchcodec.decoders.AudioDecoder.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/torchaudio/_backend/ffmpeg.py:88: UserWarning: torio.io._streaming_media_decoder.StreamingMediaDecoder has been deprecated. This deprecation is part of a large refactoring effort to transition TorchAudio into a maintenance phase. The decoding and encoding capabilities of PyTorch for both audio and video are being consolidated into TorchCodec. Please see https://github.com/pytorch/audio/issues/3902 for more information. It will be r

<_io.BufferedRandom name='segment (second pipeline).wav'>

#### 3- scipy, with a low-pass filter !

In [14]:
import scipy.signal
import soundfile as sf  # or use librosa.load/save

# Load original WAV file
original_audio, original_sr = sf.read(audioFile)
target_sr =  16_000

# apply a low-pass filter
gcd = np.gcd(original_sr, target_sr)
up = target_sr // gcd
down = original_sr // gcd

resampled_audio = scipy.signal.resample_poly(original_audio, up, down)
chunk = resampled_audio[:target_sr] #0 - > 999 = 1000 samples | select 1s -> freqancy*1s -> samples that make up 1s
if chunk.shape[0] != target_sr:
  print('lame')

#export one chunk
if os.path.exists('segment (thrid pipeline).wav'):
  os.remove('segment (thrid pipeline).wav')
sf.write("segment (thrid pipeline).wav", chunk, target_sr)

### play all of the pipelines to listen to !

In [15]:
from IPython.display import Audio
#listen to both of the audio clips
clip = Audio(audioFile, rate=16_000)
print("original: ")
display(clip)

print("Segmented, with the first segment (1s): ")
print("first pipeline: (librosa load&downsample using polyphase):")
clip = Audio("segment (first pipeline).wav", rate=16_000)
display(clip)

print("second pipeline: (torchaudio load&resample:")
clip = Audio("segment (second pipeline).wav", rate=16_000)
display(clip)

print("thrid pipeline: (scipy, with a low-pass filter !)")
clip = Audio("segment (thrid pipeline).wav", rate=16_000)
display(clip)

original: 


Segmented, with the first segment (1s): 
first pipeline: (librosa load&downsample using polyphase):


second pipeline: (torchaudio load&resample:


thrid pipeline: (scipy, with a low-pass filter !)


# Results:
as we can CLEARLY SEE
there's HEAVY alaising due to the downsampling, it's not the fault of librosa or torchaudio, it's just that dealing with mosquitoes is a hassle, very week signals with very low frequancies, the low-pass filter is the closest thing to the original recording, keeping only componants of >8000Hz (nyquist range), some background stuff with obviously all the mosquitoes intact... so to segment the files I'll use the third pipeline !